In [273]:
import pandas as pd
from rank_bm25 import BM25Okapi

In [274]:
movie_plots = pd.read_csv("data/wiki_movie_plots_deduped.csv")

In [275]:
#movie_sample = movie_plots.sample(50)

In [276]:
movie_sample = movie_plots

In [277]:
movie_sample = movie_sample.dropna(subset=['Plot', "Cast", "Director", "Genre"])

In [278]:
columns = movie_sample.columns.to_list()

for column in columns:
    try:
        movie_sample[column] = movie_sample[column].str.lower()
    except AttributeError:
        pass

/var/folders/9q/p0b6nwnd5071040x3849mdvc0000gn/T/ipykernel_88792/3115884402.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_sample[column] = movie_sample[column].str.lower()


In [279]:
movie_sample = movie_sample.rename(columns={"Title": "title"})

In [280]:
movie_sample

Release Year                            title Origin/Ethnicity  \
5              1903              alice in wonderland         american   
13             1907                     daniel boone         american   
14             1907  how brown saw the baseball game         american   
15             1907                     laughing gas         american   
16             1908         the adventures of dollie         american   
...             ...                              ...              ...   
34881          2014                the water diviner          turkish   
34882          2017              çalgı çengi i̇kimiz          turkish   
34883          2017                     olanlar oldu          turkish   
34884          2017                 non-transferable          turkish   
34885          2017              i̇stanbul kırmızısı          turkish   

                                      Director  \
5                               cecil hepworth   
13     wallace mccutcheon and ediwin s. porter   
14                                     unknown   
15                        edwin stanton porter   
16                              d. w. griffith   
...                                        ...   
34881                  director: russell crowe   
34882                           selçuk aydemir   
34883                              hakan algül   
34884                          brendan bradley   
34885                           ferzan özpetek   

                                                    Cast            Genre  \
5                                              may clark          unknown   
13                     william craven, florence lawrence     biographical   
14                                               unknown           comedy   
15                       bertha regustus, edward boulden           comedy   
16                     arthur v. johnson, linda arvidson            drama   
...                                                  ...              ...   
34881  director: russell crowe\r\ncast: russell crowe...          unknown   
34882                          ahmet kural, murat cemcir           comedy   
34883              ata demirer, tuvana türkay, ülkü duru           comedy   
34884  youtubers shanna malcolm, shira lazar, sara fl...  romantic comedy   
34885  halit ergenç, tuba büyüküstün, mehmet günsür, ...         romantic   

                                               Wiki Page  \
5      https://en.wikipedia.org/wiki/alice_in_wonderl...   
13     https://en.wikipedia.org/wiki/daniel_boone_(19...   
14     https://en.wikipedia.org/wiki/how_brown_saw_th...   
15     https://en.wikipedia.org/wiki/laughing_gas_(fi...   
16     https://en.wikipedia.org/wiki/the_adventures_o...   
...                                                  ...   
34881    https://en.wikipedia.org/wiki/the_water_diviner   
34882  https://en.wikipedia.org/wiki/%c3%87alg%c4%b1_...   
34883         https://en.wikipedia.org/wiki/olanlar_oldu   
34884  https://en.wikipedia.org/wiki/non-transferable...   
34885  https://en.wikipedia.org/wiki/%c4%b0stanbul_k%...   

                                                    Plot  
5      alice follows a large white rabbit down a "rab...  
13     boone's daughter befriends an indian maiden as...  
14     before heading out to a baseball game at a nea...  
15     the plot is that of a black woman going to the...  
16     on a beautiful summer day a father and mother ...  
...                                                  ...  
34881  the film begins in 1919, just after world war ...  
34882  two musicians, salih and gürkan, described the...  
34883  zafer, a sailor living with his mother döndü i...  
34884  the film centres around a young woman named am...  
34885  the writer orhan şahin returns to i̇stanbul af...  

[33464 rows x 8 columns]

#### Wenn man die unten angeführten rows mit None nicht löscht dann bekommt man ca. 1300 filme mehr bei der schnittmenge

In [281]:
# movie_sample.loc[movie_sample["Plot"] != "unknown"]
# movie_sample.loc[movie_sample["Cast"] != "unknown"]
# movie_sample.loc[movie_sample["Genre"] != "unknown"]
# movie_sample.loc[movie_sample["Director"] != "unknown"]

# movie_sample.loc[movie_sample["Release Year"] > 1940]

In [282]:
movie_sample

Release Year                            title Origin/Ethnicity  \
5              1903              alice in wonderland         american   
13             1907                     daniel boone         american   
14             1907  how brown saw the baseball game         american   
15             1907                     laughing gas         american   
16             1908         the adventures of dollie         american   
...             ...                              ...              ...   
34881          2014                the water diviner          turkish   
34882          2017              çalgı çengi i̇kimiz          turkish   
34883          2017                     olanlar oldu          turkish   
34884          2017                 non-transferable          turkish   
34885          2017              i̇stanbul kırmızısı          turkish   

                                      Director  \
5                               cecil hepworth   
13     wallace mccutcheon and ediwin s. porter   
14                                     unknown   
15                        edwin stanton porter   
16                              d. w. griffith   
...                                        ...   
34881                  director: russell crowe   
34882                           selçuk aydemir   
34883                              hakan algül   
34884                          brendan bradley   
34885                           ferzan özpetek   

                                                    Cast            Genre  \
5                                              may clark          unknown   
13                     william craven, florence lawrence     biographical   
14                                               unknown           comedy   
15                       bertha regustus, edward boulden           comedy   
16                     arthur v. johnson, linda arvidson            drama   
...                                                  ...              ...   
34881  director: russell crowe\r\ncast: russell crowe...          unknown   
34882                          ahmet kural, murat cemcir           comedy   
34883              ata demirer, tuvana türkay, ülkü duru           comedy   
34884  youtubers shanna malcolm, shira lazar, sara fl...  romantic comedy   
34885  halit ergenç, tuba büyüküstün, mehmet günsür, ...         romantic   

                                               Wiki Page  \
5      https://en.wikipedia.org/wiki/alice_in_wonderl...   
13     https://en.wikipedia.org/wiki/daniel_boone_(19...   
14     https://en.wikipedia.org/wiki/how_brown_saw_th...   
15     https://en.wikipedia.org/wiki/laughing_gas_(fi...   
16     https://en.wikipedia.org/wiki/the_adventures_o...   
...                                                  ...   
34881    https://en.wikipedia.org/wiki/the_water_diviner   
34882  https://en.wikipedia.org/wiki/%c3%87alg%c4%b1_...   
34883         https://en.wikipedia.org/wiki/olanlar_oldu   
34884  https://en.wikipedia.org/wiki/non-transferable...   
34885  https://en.wikipedia.org/wiki/%c4%b0stanbul_k%...   

                                                    Plot  
5      alice follows a large white rabbit down a "rab...  
13     boone's daughter befriends an indian maiden as...  
14     before heading out to a baseball game at a nea...  
15     the plot is that of a black woman going to the...  
16     on a beautiful summer day a father and mother ...  
...                                                  ...  
34881  the film begins in 1919, just after world war ...  
34882  two musicians, salih and gürkan, described the...  
34883  zafer, a sailor living with his mother döndü i...  
34884  the film centres around a young woman named am...  
34885  the writer orhan şahin returns to i̇stanbul af...  

[33464 rows x 8 columns]

In [283]:
movie_sample = movie_sample.fillna("unknown")

In [284]:
sample_list_raw = movie_sample[["title", "Director", "Cast", "Genre", "Plot"]].values.tolist()

In [285]:
delimiter = ", "
sample_list_processed = []
for nr, movie in enumerate(sample_list_raw):
    joined = delimiter.join(movie)
    joined = joined.lower()
    joined = joined.replace(",", "")
    joined = joined.replace("\r\n", "")
    joined = joined.replace(".", " ")
    joined = joined.replace("\'s", "s")
    joined = joined.replace("-", "")
    joined = joined.replace('"', '')

    sample_list_processed.append(joined)
   


In [286]:
len(sample_list_processed)


33464

In [287]:
tokenized_corpus = [doc.split(" ") for doc in sample_list_processed]

In [288]:
tokenized_corpus

[['alice',
  'in',
  'wonderland',
  'cecil',
  'hepworth',
  'may',
  'clark',
  'unknown',
  'alice',
  'follows',
  'a',
  'large',
  'white',
  'rabbit',
  'down',
  'a',
  'rabbithole',
  '',
  'she',
  'finds',
  'a',
  'tiny',
  'door',
  '',
  'when',
  'she',
  'finds',
  'a',
  'bottle',
  'labeled',
  'drink',
  'me',
  'she',
  'does',
  'and',
  'shrinks',
  'but',
  'not',
  'enough',
  'to',
  'pass',
  'through',
  'the',
  'door',
  '',
  'she',
  'then',
  'eats',
  'something',
  'labeled',
  'eat',
  'me',
  'and',
  'grows',
  'larger',
  '',
  'she',
  'finds',
  'a',
  'fan',
  'when',
  'enables',
  'her',
  'to',
  'shrink',
  'enough',
  'to',
  'get',
  'into',
  'the',
  'garden',
  'and',
  'try',
  'to',
  'get',
  'a',
  'dog',
  'to',
  'play',
  'with',
  'her',
  '',
  'she',
  'enters',
  'the',
  'white',
  'rabbits',
  'tiny',
  'house',
  'but',
  'suddenly',
  'resumes',
  'her',
  'normal',
  'size',
  '',
  'in',
  'order',
  'to',
  'get',
  'o

In [289]:
bm25 = BM25Okapi(tokenized_corpus)

#### Example BM25: 

query: "mexicanamerican family wedding" gives --> "our family wedding" as most relevant while
"mexican american family wedding" does not return this movie --> check if neural retrieval model accounts for this

In [290]:
query = "mexican american family wedding"

In [291]:
query_tokenized = query.split(" ")

In [292]:
print(query_tokenized)

['mexican', 'american', 'family', 'wedding']


In [293]:
doc_scores = bm25.get_scores(query_tokenized)

In [294]:
top_docs = bm25.get_top_n(query_tokenized, tokenized_corpus, n=10)

In [295]:
for doc in top_docs:
    print(doc)

['the', 'last', 'command', 'frank', 'lloyd', 'sterling', 'hayden', 'anna', 'maria', 'alberghetti', 'ernest', 'borgnine', 'war', 'western', 'in', '1835', 'jim', 'bowie', 'realizes', 'that', 'there', 'were', 'uneasy', 'disputes', 'between', 'the', 'mexican', 'government', 'and', 'the', 'american', 'immigrants', "who've", 'settled', 'in', 'texas', '', 'dozens', 'of', 'american', 'men', 'including', 'stephen', 'austin', 'have', 'been', 'arrested', 'for', 'supposedly', 'igniting', 'rebellions', 'against', 'the', 'mexican', 'governor', 'juan', 'almonte', 'and', 'the', 'mexican', 'garrisons', 'throughout', 'texas', '']
['a', 'doubledyed', 'deceiver', 'alfred', 'e', '', 'green', 'jack', 'pickford', 'marie', 'dunn', 'crime', 'drama', 'as', 'described', 'in', 'a', 'film', 'magazine[3]', 'the', 'llano', 'kid', '(pickford)', 'after', 'killing', 'a', 'mexican', 'in', 'texas', 'flees', 'to', 'buennas', 'tierras', 'south', 'america', '', 'the', 'american', 'counsel', 'seeking', 'to', 'rob', 'an', 'ar

*****

In [296]:
with open ("data/movies_ml.txt", "r") as f:
    movies = f.readlines()

In [297]:
movies_ml = []
for movie in movies:
    movie_dict = {}
    movie = movie.lower()
    movie = movie.replace("\n", "")
    split_list = movie.split("::")
    movie_id, title_year, genres = split_list
    movie_id = int(movie_id)
    title = title_year.split(" (")[0]
    year = title_year.split("(")[1]
    year = year.replace(")", " ")
    movie_dict["movie_id"] = movie_id
    movie_dict["title"] = title
    movie_dict["year"] = year
    movie_dict["genres"] = genres
    movies_ml.append(movie_dict)


print(movies)


        

["1::Toy Story (1995)::Animation|Children's|Comedy\n", "2::Jumanji (1995)::Adventure|Children's|Fantasy\n", '3::Grumpier Old Men (1995)::Comedy|Romance\n', '4::Waiting to Exhale (1995)::Comedy|Drama\n', '5::Father of the Bride Part II (1995)::Comedy\n', '6::Heat (1995)::Action|Crime|Thriller\n', '7::Sabrina (1995)::Comedy|Romance\n', "8::Tom and Huck (1995)::Adventure|Children's\n", '9::Sudden Death (1995)::Action\n', '10::GoldenEye (1995)::Action|Adventure|Thriller\n', '11::American President, The (1995)::Comedy|Drama|Romance\n', '12::Dracula: Dead and Loving It (1995)::Comedy|Horror\n', "13::Balto (1995)::Animation|Children's\n", '14::Nixon (1995)::Drama\n', '15::Cutthroat Island (1995)::Action|Adventure|Romance\n', '16::Casino (1995)::Drama|Thriller\n', '17::Sense and Sensibility (1995)::Drama|Romance\n', '18::Four Rooms (1995)::Thriller\n', '19::Ace Ventura: When Nature Calls (1995)::Comedy\n', '20::Money Train (1995)::Action\n', '21::Get Shorty (1995)::Action|Comedy|Drama\n', '22:

In [298]:
movies_ml = pd.DataFrame(movies_ml)

In [299]:
movies_ml

movie_id                        title   year  \
0            1                    toy story  1995    
1            2                      jumanji  1995    
2            3             grumpier old men  1995    
3            4            waiting to exhale  1995    
4            5  father of the bride part ii  1995    
...        ...                          ...    ...   
3878      3948             meet the parents  2000    
3879      3949          requiem for a dream  2000    
3880      3950                    tigerland  2000    
3881      3951             two family house  2000    
3882      3952               contender, the  2000    

                            genres  
0      animation|children's|comedy  
1     adventure|children's|fantasy  
2                   comedy|romance  
3                     comedy|drama  
4                           comedy  
...                            ...  
3878                        comedy  
3879                         drama  
3880                         drama  
3881                         drama  
3882                drama|thriller  

[3883 rows x 4 columns]

In [300]:
merged_movie_df = pd.merge(movies_ml, movie_sample, on="title", how="inner")

In [301]:
movie_ids = merged_movie_df["movie_id"].values.tolist()

In [302]:
with open ("data/ratings_ml.txt", "r") as f:
    ratings = f.readlines()

In [303]:
ratings_list = []
for rating in ratings:
    rating_dict = {}
    rating = rating.replace("\n", "")
    split_list = rating.split("::")
    split_list_clean = []
    for r in split_list:
        r = int(r)
        split_list_clean.append(r)

    user_id, movie_id, rating, timestamp = split_list_clean
    rating_dict["user_id"] = user_id
    rating_dict["movie_id"] = movie_id
    rating_dict["rating"] = rating
    rating_dict["timestamp"] = timestamp
    ratings_list.append(rating_dict)

In [304]:
ratings_df = pd.DataFrame(ratings_list)
ratings_filtered = ratings_df.loc[ratings_df["movie_id"].isin(movie_ids)]


In [305]:
ratings_filtered

user_id  movie_id  rating  timestamp
0              1      1193       5  978300760
1              1       661       3  978302109
2              1       914       3  978301968
3              1      3408       4  978300275
6              1      1287       5  978302039
...          ...       ...     ...        ...
1000203     6040      1090       3  956715518
1000204     6040      1091       1  956716541
1000206     6040       562       5  956704746
1000207     6040      1096       4  956715648
1000208     6040      1097       4  956715569

[679919 rows x 4 columns]

In [306]:
ratings_filtered["rating"].value_counts()

rating
4    236403
3    181583
5    146425
2     76000
1     39508
Name: count, dtype: int64

In [307]:
ratings_filtered["rating"].mean()

3.5504140934434836

In [308]:
users_with_valid_ratings = list(set(ratings_filtered["user_id"].values.tolist()))

In [309]:
with open ("data/users_ml.txt", "r") as f:
    users = f.readlines()

In [310]:
users_list = []
for user in users:
    user_dict = {}
    user = user.replace("\n", "")
    split_list = user.split("::")
    split_list_clean = []
    for u in split_list:
        try:
            u = int(u)
            split_list_clean.append(u)
        except ValueError:
            split_list_clean.append(u)
    
    user_id, gender, age, occupation, zip_code = split_list_clean
    user_dict["user_id"] = user_id
    user_dict["gender"] = gender
    user_dict["age"] = age
    user_dict["occupation"] = occupation
    user_dict["zip_code"] = zip_code
    users_list.append(user_dict)

In [311]:
users_df = pd.DataFrame(users_list)
users_df

user_id gender  age  occupation zip_code
0           1      F    1          10    48067
1           2      M   56          16    70072
2           3      M   25          15    55117
3           4      M   45           7     2460
4           5      M   25          20    55455
...       ...    ...  ...         ...      ...
6035     6036      F   25          15    32603
6036     6037      F   45           1    76006
6037     6038      F   56           1    14706
6038     6039      F   45           0     1060
6039     6040      M   25           6    11106

[6040 rows x 5 columns]

In [312]:
users_filtered = users_df.loc[users_df["user_id"].isin(users_with_valid_ratings)]
users_filtered

user_id gender  age  occupation zip_code
0           1      F    1          10    48067
1           2      M   56          16    70072
2           3      M   25          15    55117
3           4      M   45           7     2460
4           5      M   25          20    55455
...       ...    ...  ...         ...      ...
6035     6036      F   25          15    32603
6036     6037      F   45           1    76006
6037     6038      F   56           1    14706
6038     6039      F   45           0     1060
6039     6040      M   25           6    11106

[6040 rows x 5 columns]